In [6]:
# 读取配置
# from config_jingbo import *
# from config_tansuanli import *
from config_juxiting import *
from lib.dataread import *
from lib.tools import *
from models.nerulforcastmodels import ex_Model,model_losss,brent_export_pdf,tansuanli_export_pdf,pp_export_pdf,model_losss_juxiting

import glob
import torch
torch.set_float32_matmul_precision("high")

sqlitedb = SQLiteHandler(db_name) 
sqlitedb.connect()


signature = BinanceAPI(APPID, SECRET)
etadata = EtaReader(signature=signature,
                        classifylisturl = classifylisturl,
                        classifyidlisturl=classifyidlisturl,
                        edbcodedataurl=edbcodedataurl,
                        edbcodelist=edbcodelist,
                        edbdatapushurl=edbdatapushurl,
                        edbdeleteurl=edbdeleteurl,
                        edbbusinessurl=edbbusinessurl
                        )
# 获取数据
if is_eta:
    # eta数据
    logger.info('从eta获取数据...')
    signature = BinanceAPI(APPID, SECRET)
    etadata = EtaReader(signature=signature,
                                classifylisturl = classifylisturl,
                                classifyidlisturl=classifyidlisturl,
                                edbcodedataurl=edbcodedataurl,
                                edbcodelist=edbcodelist,
                                edbdatapushurl=edbdatapushurl,
                                edbdeleteurl=edbdeleteurl,
                                edbbusinessurl=edbbusinessurl,
                                )

    df_zhibiaoshuju,df_zhibiaoliebiao = etadata.get_eta_api_yuanyou_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理
    # df_zhibiaoshuju,df_zhibiaoliebiao =  etadata.get_eta_api_pp_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理

    
    # 数据处理
    df = datachuli(df_zhibiaoshuju,df_zhibiaoliebiao,y = y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time) 

else:
    logger.info('读取本地数据：'+os.path.join(dataset,data_set))
    df = getdata(filename=os.path.join(dataset,data_set),y=y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time)  # 原始数据，未处理

# 更改预测列名称
df.rename(columns={y:'y'},inplace=True)
    
if is_edbnamelist:
    df = df[edbnamelist]     
df.to_csv(os.path.join(dataset,'指标数据.csv'), index=False)
# 保存最新日期的y值到数据库
# 取第一行数据存储到数据库中
first_row = df[['ds','y']].tail(1)
# 将最新真实值保存到数据库
if not sqlitedb.check_table_exists('trueandpredict'):
    first_row.to_sql('trueandpredict',sqlitedb.connection,index=False)
else:
    for row in first_row.itertuples(index=False):
        row_dict = row._asdict()
        check_query = sqlitedb.select_data('trueandpredict',where_condition = f"ds = '{row.ds}'")
        if len(check_query) > 0:
            set_clause = ", ".join([f"{key} = '{value}'" for key, value in row_dict.items()])
            sqlitedb.update_data('trueandpredict',set_clause,where_condition = f"ds = '{row.ds}'")
            continue
        sqlitedb.insert_data('trueandpredict',tuple(row_dict.values()),columns=row_dict.keys())

import datetime
# 判断当前日期是不是周一
is_weekday = datetime.datetime.now().weekday() == 3
if is_weekday:
    logger.info('今天是周一，更新预测模型')
    # 计算最近20天预测残差最低的模型名称

    model_results = sqlitedb.select_data('trueandpredict',order_by = "ds DESC",limit = "20")
    model_results = model_results.dropna()
    modelnames  = model_results.columns.to_list()[2:] 
    for col in model_results[modelnames].select_dtypes(include=['object']).columns:
        model_results[col] = model_results[col].astype(np.float32)
    # 计算每个预测值与真实值之间的偏差率
    for model in modelnames:
        model_results[f'{model}_abs_error_rate'] = abs(model_results['y'] - model_results[model]) / model_results['y']

    # 获取每行对应的最小偏差率值
    min_abs_error_rate_values = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].min(), axis=1)
    # 获取每行对应的最小偏差率值对应的列名
    min_abs_error_rate_column_name = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].idxmin(), axis=1)
    # 将列名索引转换为列名
    min_abs_error_rate_column_name = min_abs_error_rate_column_name.map(lambda x: x.split('_')[0])
    # 取出现次数最多的模型名称
    most_common_model = min_abs_error_rate_column_name.value_counts().idxmax()
    logger.info(f"最近20天预测残差最低的模型名称：{most_common_model}")

    # 保存结果到数据库
    
    if not sqlitedb.check_table_exists('most_model'):
        sqlitedb.create_table('most_model',columns="ds datetime, most_common_model TEXT")
    sqlitedb.insert_data('most_model',(datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S'),most_common_model,),columns=('ds','most_common_model',))






if is_corr:
    df = corr_feature(df=df)

df1 = df.copy()  # 备份一下，后面特征筛选完之后加入ds y 列用
logger.info(f"开始训练模型...")
row,col = df.shape

now = datetime.datetime.now().strftime('%Y%m%d%H%M%S')




读取本地数据：dataset\PP指标数据.xlsx
读取本地数据：dataset\PP指标数据.xlsx
getdata接收：dataset\PP指标数据.xlsx date 
getdata接收：dataset\PP指标数据.xlsx date 
删除两月不更新特征前数据量：(2502, 355)
删除两月不更新特征前数据量：(2502, 355)
删除两月不更新特征后数据量：(2502, 323)
删除两月不更新特征后数据量：(2502, 323)
删除预测列为空值的行后数据量：(654, 323)
删除预测列为空值的行后数据量：(654, 323)
删除全为空值的列后数据量：(654, 323)
删除全为空值的列后数据量：(654, 323)
d:\code\PriceForecast\lib\dataread.py:135: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  values.dropna(inplace=True,axis=0)
d:\code\PriceForecast\lib\dataread.py:135: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  values.dropna(inplace=True,axis=0)
d:\code\PriceForecast\lib\dataread.py:135: Setti

OperationalError: database is locked

In [ ]:

df1 = df.copy()  # 备份一下，后面特征筛选完之后加入ds y 列用
logger.info(f"开始训练模型...")
row,col = df.shape

now = datetime.datetime.now().strftime('%Y%m%d%H%M%S')
ex_Model(df,
        horizon=horizon,
        input_size=input_size,
        train_steps=train_steps,
        val_check_steps=val_check_steps,
        early_stop_patience_steps=early_stop_patience_steps,
        is_debug=is_debug,
        dataset=dataset,
        is_train=is_train,
        is_fivemodels=is_fivemodels,
        val_size=val_size,
        test_size=test_size,
        settings=settings,
        now=now,
        etadata = etadata,
        modelsindex = modelsindex,
        data = data,
        is_eta=is_eta,
        )

In [5]:
model_results3 = model_losss_juxiting(sqlitedb)


d:\code\PriceForecast\models\nerulforcastmodels.py:617: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  f.write(','.join(modelnames) + '\n')
posx and posy should be finite values


Column 'ds' already exists in table 'trueandpredict'.
Column 'NHITS' already exists in table 'trueandpredict'.
Column 'Informer' already exists in table 'trueandpredict'.
Column 'LSTM' already exists in table 'trueandpredict'.
Column 'iTransformer' already exists in table 'trueandpredict'.
Column 'TSMixer' already exists in table 'trueandpredict'.
Column 'TSMixerx' already exists in table 'trueandpredict'.
Column 'PatchTST' already exists in table 'trueandpredict'.
Column 'RNN' already exists in table 'trueandpredict'.
Column 'GRU' already exists in table 'trueandpredict'.
Column 'TCN' already exists in table 'trueandpredict'.
Column 'BiTCN' already exists in table 'trueandpredict'.
Column 'DilatedRNN' already exists in table 'trueandpredict'.
Column 'MLP' already exists in table 'trueandpredict'.
Column 'DLinear' already exists in table 'trueandpredict'.
Column 'NLinear' already exists in table 'trueandpredict'.
Column 'TFT' already exists in table 'trueandpredict'.
Column 'FEDformer'

posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values


In [ ]:
# 基于梯度计算特征的权重


